# **Tarea 3 - Word Embeddings 📚**

**Integrantes:**

**Fecha límite de entrega 📆:** 3 de mayo.

**Tiempo estimado de dedicación:**


**Instrucciones:**
- El ejercicio consiste en:
    - Responder preguntas relativas a los contenidos vistos en los vídeos y slides de las clases. 
    - Entrenar Word2Vec y Word Context Matrix sobre un pequeño corpus.
    - Evaluar los embeddings obtenidos en una tarea de clasificación.
- La tarea se realiza en grupos de **máximo** 2 personas. Puede ser invidivual pero no es recomendable.
- La entrega es a través de u-cursos a más tardar el día estipulado arriba. No se aceptan atrasos.
- El formato de entrega es este mismo Jupyter Notebook.
- Al momento de la revisión tu código será ejecutado. Por favor verifica que tu entrega no tenga errores de compilación. 
- En el horario de auxiliar pueden realizar consultas acerca de la tarea a través del canal de Discord del curso. 


**Referencias**

Vídeos: 

- [Linear Models](https://youtu.be/zhBxDsNLZEA)
- [Neural Networks](https://youtu.be/oHZHA8h2xN0)
- [Word Embeddings](https://youtu.be/wtwUsJMC9CA)

## **Preguntas teóricas 📕 (2 puntos).** ##
Para estas preguntas no es necesario implementar código, pero pueden utilizar pseudo código.

### **Parte 1: Modelos Lineales (1 ptos)**

Suponga que tiene un dataset de 10.000 documentos etiquetados por 4 categorías: política, deporte, negocios y otros. 

**Pregunta 1**: Diseñe un modelo lineal capaz de clasificar un documento según estas categorías donde el output sea un vector con una distribución de probabilidad con la pertenencia a cada clase. 

Especifique: representación de los documentos de entrada, parámetros del modelo, transformaciones necesarias para obtener la probabilidad de cada etiqueta y función de pérdida escogida. **(0.5 puntos)**

**Respuesta**: 


**Pregunta 2**: Explique cómo funciona el proceso de entrenamiento en este tipo de modelos y su evaluación. **(0.5 puntos)**

**Respuesta**: 

### **Parte 2: Redes Neuronales (1 ptos)** 

Supongamos que tenemos la siguiente red neuronal.

![image.png](https://drive.google.com/uc?export=view&id=1fFTjtMvH6MY8o42_vj010y8eTuCVb5a3)

**Pregunta 1**: En clases les explicaron como se puede representar una red neuronal de una y dos capas de manera matemática. Dada la red neuronal anterior, defina la salida $\vec{\hat{y}}$ en función del vector $\vec{x}$, pesos $W^i$, bias $b^i$ y funciones $g,f,h$. 

Adicionalmente liste y explicite las dimensiones de cada matriz y vector involucrado en la red neuronal. **(0.5 Puntos)**

**Respuesta**: 

Formula:
$\vec{\hat{y}} = NN_{MLP3}(\vec{x}) =$

Dimensiones: 

**Pregunta 2**: Explique qué es backpropagation. ¿Cuales serían los parámetros a evaluar en la red neuronal anterior durante backpropagation? **(0.25 puntos)**

**Respuesta**:

**Pregunta 3**: Explique los pasos de backpropagation. En la red neuronal anterior: Cuales son las derivadas que debemos calcular para poder obtener $\vec{\delta^l_{[j]}}$ en todas las capas? **(0.25 puntos)**

**Respuesta**:

## **Preguntas prácticas 💻 (4 puntos).** ##

### **Parte 3: Word Embeddings**

En la auxiliar 2 se nombraron dos formas de crear word vectors:

-  Distributional Vectors.
-  Distributed Vectors.

El objetivo de esta parte es comparar las dos embeddings obtenidos de estas dos estrategias en una tarea de clasificación.

In [19]:
import re  
import pandas as pd 
from time import time  
from collections import defaultdict 
import string 
import multiprocessing
import os
import gensim
import sklearn
from sklearn import linear_model
from collections import Counter
import numpy as np
import scipy
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score, confusion_matrix, cohen_kappa_score, classification_report

# word2vec
from gensim.models import Word2Vec, KeyedVectors, FastText
from gensim.models.phrases import Phrases, Phraser
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
import logging

logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
logger = logging.getLogger(__name__)

#### **Parte A (1 punto)** 

En esta parte debe crear una matriz palabra contexto, para esto, complete el siguiente template (para esta parte puede utilizar las librerías ```numpy``` y/o ```scipy```). Hint: revise como utilizar matrices sparse de ```scipy```

```python
class WordContextMatrix:

  def __init__(self, vocab_size, window_size, dataset, tokenizer):
    # se sugiere agregar un una estructura de datos para guardar las
    # palabras del vocab y para guardar el conteo de coocurrencia
    ...
    
  def add_word_to_vocab(self, word):
    # Le puede ser útil considerar un token unk al vocab
    # para palabras fuera del vocab
    ...
  
  def build_matrix(self):
    ...

  def matrix2dict(self):
    # se recomienda transformar la matrix a un diccionario de embedding.
    ...

```

puede modificar los parámetros o métodos si lo considera necesario. Para probar la matrix puede utilizar el siguiente corpus.

```python
corpus = [
  "I like deep learning.",
  "I like NLP.",
  "I enjoy flying."
]
```

Obteniendo una matriz parecia a esta:

***Resultado esperado***: 

| counts   | I  | like | enjoy | deep | learning | NLP | flying | . |   
|----------|---:|-----:|------:|-----:|---------:|----:|-------:|--:|
| I        | 0  |  2   |  1    |    0 |  0       |   0 | 0      | 0|            
| like     |  2 |    0 |  0    |    1 |  0       |   1 | 0      | 0 | 
| enjoy    |  1 |    0 |  0    |    0 |  0       |   0 | 1      | 0 |
| deep     |  0 |    1 |  0    |    0 |  1       |   0 | 0      | 0 |  
| learning |  0 |    0 |  0    |    1 |  0       |   0 | 0      | 1 |          
| NLP      |  0 |    1 |  0    |    0 |  0       |   0 | 0      | 1 |
| flying   |  0 |    0 |  1    |    0 |  0       |   0 | 0      | 1 | 
| .        |  0 |    0 |  0    |    0 |  1       |   1 | 1      | 0 | 

``

**Respuesta:**

In [3]:
class WordContextMatrix:
  def __init__(self, vocab_size, window_size, dataset, tokenizer):
    # se inicializa la matriz de palabra-contexto dado un dataset,
    # un tokenizador, y el tamaño del vocabulario.
    self.current_word_index = 0
    self.vocab_size = vocab_size
    self.WCMatrix = np.zeros((vocab_size, vocab_size), dtype = int)
    self.vocab = np.empty(vocab_size, dtype=object)
    self.window_size = window_size
    self.dataset = dataset
    self.tokenizer = tokenizer

    # se define una palabra como desconocida
    self.vocab[self.vocab_size - 1] = 'unk'
    

  def add_word_to_vocab(self, word):
    # funcion que añade una palabra al vocabulario
    # si solo queda un espacio en el vocabulario, se añade
    if self.current_word_index < self.vocab_size - 1:
      self.vocab[self.current_word_index] = word
      self.current_word_index += 1
    
  
  def build_matrix(self):
    # se construye la matriz de embedding
    
    # primero se recorren las palabras del dataset ya 
    # tokenizadas y se añaden al vocabulario.
    for i in range(0, len(self.dataset)):
      document = self.tokenizer(self.dataset[i])
      for j in range(0, len(document)):
        # se busca si la palabra ya está en el vocabulario
        new_word_index = None
        for k in range(0, self.current_word_index):
          # si la palabra ya está en el vocabulario, se obtiene su indice
          if document[j] == self.vocab[k]:
            new_word_index = k
            break
        # si la palabra no está en el vocabulario, se añade
        if new_word_index == None:
          self.add_word_to_vocab(document[j])
          new_word_index = self.current_word_index - 1

        # se visitan las self.window_size de palabras que rodean
        # a la palabra actual, y se aumenta en uno el contador
        # de la matrix en las posiciones [new_word_index, word_index] 
        # y [word_index, new_word_index]
        for contxt_wrd_indx in range((max(0, j - self.window_size)), 
                                     (min(len(document), j + self.window_size + 1))):
          word_index = None
          # se obtiene el índice de la palabra en el vocabulario
          for k in range(0, self.current_word_index):
            if self.vocab[k] == document[contxt_wrd_indx]:
              word_index = k
              break
          # si no se encontró un índice
          if word_index == None:
            # si hay espacio en el vocabulario, se añade
            if self.current_word_index < self.vocab_size - 1:
              self.add_word_to_vocab(document[contxt_wrd_indx])
              word_index = self.current_word_index - 1
            else: # si no, se toma el índice de la palabra desconocida
              word_index = self.vocab_size - 1

          # se aumenta en uno el contador de la matrix en las posiciones mencionadas
          if contxt_wrd_indx != j:
            self.WCMatrix[new_word_index, word_index] += 1
            self.WCMatrix[word_index, new_word_index] += 1
    # debido a que cada interacción word-word se cuenta dos veces, se divide entre dos
    self.WCMatrix = self.WCMatrix // 2

  def matrix2dict(self):
    # se transforma la matrix a un diccionario de embedding.
    embbeding_dict = {}
    for i in range(self.current_word_index):
      # se obtiene el vector de embedding de la palabra
      # y se añade al diccionario
      embbeding_dict[self.vocab[i]] = self.WCMatrix[i, :]
    return embbeding_dict
      



In [5]:
from nltk.tokenize import wordpunct_tokenize 
corpus = [
  "I like deep learning.",
  "I like NLP.",
  "I enjoy flying."
]

CorpusWCM = WordContextMatrix(vocab_size=9, window_size=1, dataset=corpus, tokenizer=wordpunct_tokenize)
CorpusWCM.build_matrix()
print("Vocabulario: ", CorpusWCM.vocab)
print("Matriz de embedding: \n", CorpusWCM.WCMatrix)
print("Diccionario de embedding: \n", CorpusWCM.matrix2dict())

Vocabulario:  ['I' 'like' 'deep' 'learning' '.' 'NLP' 'enjoy' 'flying' 'unk']
Matriz de embedding: 
 [[0 2 0 0 0 0 1 0 0]
 [2 0 1 0 0 1 0 0 0]
 [0 1 0 1 0 0 0 0 0]
 [0 0 1 0 1 0 0 0 0]
 [0 0 0 1 0 1 0 1 0]
 [0 1 0 0 1 0 0 0 0]
 [1 0 0 0 0 0 0 1 0]
 [0 0 0 0 1 0 1 0 0]
 [0 0 0 0 0 0 0 0 0]]
Diccionario de embedding: 
 {'I': array([0, 2, 0, 0, 0, 0, 1, 0, 0], dtype=int32), 'like': array([2, 0, 1, 0, 0, 1, 0, 0, 0], dtype=int32), 'deep': array([0, 1, 0, 1, 0, 0, 0, 0, 0], dtype=int32), 'learning': array([0, 0, 1, 0, 1, 0, 0, 0, 0], dtype=int32), '.': array([0, 0, 0, 1, 0, 1, 0, 1, 0], dtype=int32), 'NLP': array([0, 1, 0, 0, 1, 0, 0, 0, 0], dtype=int32), 'enjoy': array([1, 0, 0, 0, 0, 0, 0, 1, 0], dtype=int32), 'flying': array([0, 0, 0, 0, 1, 0, 1, 0, 0], dtype=int32)}


#### **Parte B (1.5 puntos)**

En esta parte es debe entrenar Word2Vec de gensim y construir la matriz palabra contexto utilizando el dataset de diálogos de los Simpson. 

Utilizando el dataset adjunto con la tarea:

In [6]:
data_file = "dialogue-lines-of-the-simpsons.zip"
df = pd.read_csv(data_file)
stopwords = pd.read_csv(
    'https://raw.githubusercontent.com/Alir3z4/stop-words/master/english.txt'
).values
stopwords = Counter(stopwords.flatten().tolist())
df = df.dropna().reset_index(drop=True) # Quitar filas vacias

**Pregunta 1**: Ayudándose de los pasos vistos en la auxiliar, entrene los modelos Word2Vec. **(0.75 punto)** (Hint, le puede servir explorar un poco los datos)

**Respuesta**:

In [7]:
df.head()

raw_character_text                                       spoken_words
0              Miss Hoover  No, actually, it was a little of both. Sometim...
1             Lisa Simpson                             Where's Mr. Bergstrom?
2              Miss Hoover  I don't know. Although I'd sure like to talk t...
3             Lisa Simpson                         That life is worth living.
4  Edna Krabappel-Flanders  The polls will be open from now until the end ...

In [8]:
# se elimina la columna que no contiene los datos importantes
new_df = df.drop('raw_character_text', axis=1)

# se verifica que no hayan valores nulos
new_df.isnull().values.any()

False

In [9]:
CorpusSimsons = WordContextMatrix(vocab_size=1000, window_size=3, dataset=new_df['spoken_words'].values.tolist(), tokenizer=wordpunct_tokenize)
CorpusSimsons.build_matrix()


In [10]:
print("Matriz de embedding: \n", CorpusSimsons.WCMatrix)
print("Diccionario de embedding: ", CorpusSimsons.matrix2dict())

Matriz de embedding: 
 [[   236   2147      7 ...      0    973    973]
 [  2147  20412    122 ...     21  57623  57613]
 [     7    122      0 ...      0    147    147]
 ...
 [     0     21      0 ...      0    111    110]
 [   973  57623    147 ...    111     62 327479]
 [   973  57613    147 ...    110 327479      0]]
Diccionario de embedding:  {'No': array([ 236, 2147,    7,  157,   40,   58,    7,   30,    2, 1547,    0,
          1,    1,   58,   29,    9,   90,    0,   20,    0,    2,  585,
         80,    3,    0,   91,  191,    9,   14,    3,   16,    0,  172,
        521,   78,    5,    9,    0,    0,    2,   14,   49,    3,    4,
         11,   32,    1,   25,    2,    0,   39,    9,   47,    0,   19,
          0,    1,    4,   23,    0,   19,   11,    1,    2,   12,    4,
          0,    0,    9,   28,    0,    2,    0,    0,    2,    2,   27,
         46,    1,    3,    0,    0,    0,   17,    2,    1,    8,   41,
          0,    3,    1,    1, 1038,    7,    4,    0,    6

**Pregunta 2**: Cree una matriz palabra contexto usando el mismo dataset. Configure el largo del vocabulario a 1000 o 2000 tokens, puede agregar valores mayores pero tenga en cuenta que la construcción de la matriz puede tomar varios minutos. Puede que esto tarde un poco. **(0.75 punto)** 

**Respuesta:**

In [11]:
CorpusSimsons2 = WordContextMatrix(vocab_size=2000, window_size=3, dataset=new_df['spoken_words'].values.tolist(), tokenizer=wordpunct_tokenize)
CorpusSimsons2.build_matrix()
print("Vocabulario: ", CorpusSimsons.vocab)

Vocabulario:  ['No' ',' 'actually' 'it' 'was' 'a' 'little' 'of' 'both' '.' 'Sometimes'
 'when' 'disease' 'is' 'in' 'all' 'the' 'magazines' 'and' 'news' 'shows'
 "'" 's' 'only' 'natural' 'that' 'you' 'think' 'have' 'Where' 'Mr'
 'Bergstrom' '?' 'I' 'don' 't' 'know' 'Although' 'd' 'sure' 'like' 'to'
 'talk' 'him' 'He' 'didn' 'touch' 'my' 'lesson' 'plan' 'What' 'did' 'he'
 'teach' 'That' 'life' 'worth' 'living' 'The' 'polls' 'will' 'be' 'open'
 'from' 'now' 'until' 'end' 'recess' 'Now' 'just' 'case' 'any' 'decided'
 'put' 'thought' 'into' 'this' 'we' 'll' 'our' 'final' 'statements'
 'Martin' 'there' 'anything' 'left' 'say' 'Bart' 'Victory' 'party' 'under'
 'slide' '!' 'Hey' 'hey' 'Moved' 'out' 'morning' 'must' 'new' 'job' '--'
 'took' 'his' 'Copernicus' 'costume' 'Do' 'where' 'could' 'find' 'taking'
 'next' 'train' 'Capital' 'City' 'how' '...' 'traditional' 'yet'
 'environmentally' 'sound' 'Yes' 'been' 'backbone' 'country' 'since'
 'Leland' 'Stanford' 'drove' 'golden' 'spike' 'at' 'Promon

#### **Parte C (1.5 puntos): Aplicar embeddings para clasificar**

Ahora utilizaremos los embeddings que acabamos de calcular para clasificar palabras basadas en su polaridad (positivas o negativas). 

Para esto ocuparemos el lexicón AFINN incluido en la tarea, que incluye una lista de palabras y un 1 si su connotación es positiva y un -1 si es negativa.

In [12]:
AFINN = 'AFINN_full.csv'
df_afinn = pd.read_csv(AFINN, sep='\t', header=None)

Hint: Para w2v y la wcm son esperables KeyErrors debido a que no todas las palabras del corpus de los simpsons tendrán una representación en AFINN. Para el caso de la matriz palabra contexto se recomienda convertir su matrix a un diccionario. Pueden utilizar esta función auxiliar para filtrar las filas en el dataframe que no tienen embeddings (como w2v no tiene token UNK se deben ignorar).

In [13]:
def try_apply(model,word):
    try:
        aux = model[word]
        return True
    except KeyError:
        # logger.error('Word {} not in dictionary'.format(word))
        return False

**Pregunta 1**: Transforme las palabras del corpus de AFINN a la representación en embedding que acabamos de calcular (con ambos modelos). 

Su dataframe final debe ser del estilo [embedding, sentimiento], donde los embeddings corresponden a $X$ y el sentimiento asociado con el embedding a $y$ (positivo/negativo, 1/-1). 

Para ambos modelos, separar train y test de acuerdo a la siguiente función. **(0.5 puntos)**

In [26]:
embb_dict1 = CorpusSimsons.matrix2dict()
embb_dict2 = CorpusSimsons2.matrix2dict()
main_df1 = pd.DataFrame(columns=['palabra', 'embeding', 'sentimiento'])
main_df2 = pd.DataFrame(columns=['palabra', 'embeding', 'sentimiento'])
for word in df_afinn[0].values.tolist():
    if try_apply(embb_dict1, word):
        main_df1 = main_df1.append({'palabra': word, 'embeding': embb_dict1[word], 
                                    'sentimiento': df_afinn[1][df_afinn[0] == word].values[0]}, ignore_index=True)
    if try_apply(embb_dict2, word):
        main_df2 = main_df2.append({'palabra': word, 'embeding': embb_dict2[word], 
                                    'sentimiento': df_afinn[1][df_afinn[0] == word].values[0]}, ignore_index=True)    

print(main_df1.head())
print(main_df2.head())

    palabra                                           embeding sentimiento
0    loving  [0, 22, 0, 0, 0, 14, 1, 9, 0, 26, 0, 1, 0, 3, ...           1
1     fools  [0, 4, 0, 0, 0, 0, 0, 1, 0, 8, 0, 0, 0, 0, 0, ...          -1
2     lucky  [0, 37, 0, 3, 5, 14, 2, 4, 0, 55, 0, 1, 0, 14,...           1
3    forgot  [0, 54, 0, 7, 2, 3, 0, 2, 0, 54, 0, 0, 0, 1, 3...          -1
4  annoying  [0, 6, 0, 0, 0, 1, 0, 2, 0, 15, 0, 0, 0, 4, 1,...          -1
      palabra                                           embeding sentimiento
0      loving  [0, 22, 0, 0, 0, 14, 1, 9, 0, 26, 0, 1, 0, 3, ...           1
1       stuck  [0, 12, 0, 10, 3, 20, 0, 4, 0, 32, 0, 0, 0, 5,...          -1
2       funny  [1, 92, 2, 24, 14, 35, 4, 13, 1, 156, 0, 6, 0,...           1
3        fame  [0, 3, 0, 0, 1, 1, 0, 4, 0, 7, 0, 0, 0, 1, 0, ...           1
4  advantages  [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, ...           1


```python
X_train1, X_test1, y_train1, y_test1 = train_test_split(X, y, random_state=0, test_size=0.1, stratify=y)
```


**Respuesta**:

In [27]:
X_train1, X_test1, y_train1, y_test1 = train_test_split(main_df1['embeding'].values.tolist(), main_df1['sentimiento'].values.tolist(), 
                                                        random_state=0, test_size=0.1, stratify=main_df1['sentimiento'].values.tolist())
X_train2, X_test2, y_train2, y_test2 = train_test_split(main_df2['embeding'].values.tolist(), main_df2['sentimiento'].values.tolist(), 
                                                        random_state=0, test_size=0.1, stratify=main_df2['sentimiento'].values.tolist())

**Pregunta 2**: Entrenar una regresión logística (vista en auxiliar) y reportar accuracy, precision, recall, f1 y confusion_matrix para ambos modelos. Por qué se obtienen estos resultados? Cómo los mejorarías? Como podrías mejorar los resultados de la matriz palabra contexto? es equivalente al modelo word2vec? **(1 punto)**

**Respuesta**:

In [28]:
clf = LogisticRegression(max_iter=1000000)

pipeline1 = Pipeline([('clf', clf)])
pipeline1.fit(X_train1, y_train1)
y_pred1 = pipeline1.predict(X_test1)
conf_matrix1 = confusion_matrix(y_test1, y_pred1)
print('-------------- Modelo 1 --------------')
print(conf_matrix1)
print(classification_report(y_test1, y_pred1))

pipeline2 = Pipeline([('clf', clf)])
pipeline2.fit(X_train2, y_train2)
y_pred2 = pipeline2.predict(X_test2)
conf_matrix2 = confusion_matrix(y_test2, y_pred2)
print('-------------- Modelo 2 --------------')
print(conf_matrix2)
print(classification_report(y_test2, y_pred2))

-------------- Modelo 1 --------------
[[3 3]
 [2 3]]
              precision    recall  f1-score   support

          -1       0.60      0.50      0.55         6
           1       0.50      0.60      0.55         5

    accuracy                           0.55        11
   macro avg       0.55      0.55      0.55        11
weighted avg       0.55      0.55      0.55        11

-------------- Modelo 2 --------------
[[9 3]
 [4 7]]
              precision    recall  f1-score   support

          -1       0.69      0.75      0.72        12
           1       0.70      0.64      0.67        11

    accuracy                           0.70        23
   macro avg       0.70      0.69      0.69        23
weighted avg       0.70      0.70      0.69        23



Se obtienen mejores resultados con el segundo modelo, pues este contiene más palabras en el vocabulario que el primero, permitiendo mayor representación y embeddings para más palabras del dataset original. Para mejorar estos resultados, aumentaría en primer lugar el tamaño del vocabulario para reducir el uso de la palabra comodín 'unk' (permitiendo mayor representación y significado individual de cada palabra), y además aumentar la ventana de contexto para que se pueda obtener mayor información de las palabras.

Las modificaciones anteriores mejorarían directamente los resultados de la matriz palabra contexto, pues como ya se mencionó, al aumentar el vocabulario y aumentar la ventana de contexto, se obtienen mejores representaciones de cada palabra y aumenta la cantidad de palabras que se pueden clasificar.

Finalmente este modelo es equivalente al modelo word2vec, pero en el sentido del uso de vectores para la clasificación y el calculo de distancia entre palabras. Si se habla en el sentido de representación de documentos y de significado, Word Embeddings es totalmente distinto a Word2Vec.